In [11]:

import logging
from tqdm import tqdm
import numpy as np

import torch
import torch.nn as nn
from torch.utils.data import DataLoader

from models import Model
from data.dataset import ResponseSelectionDataset
from models.utils.checkpointing import load_checkpoint
from models.utils.scorer import calculate_candidates_ranking, logits_mrr, logits_recall_at_k

class Evaluation(object):
    def __init__(self, hparams, model=None, split = "test"):

        self.hparams = hparams
        self.model = model
        self._logger = logging.getLogger(__name__)
        self.device = (torch.device("cuda", self.hparams.gpu_ids[0])
        if self.hparams.gpu_ids[0] >= 0 else torch.device("cpu"))
        self.split = split
        print("Evaluation Split :", self.split)

        do_valid, do_test = False, False
        if split == "valid":
            do_valid = True
        else:
            do_test = True
        self._build_dataloader(do_valid=do_valid, do_test=do_test)
        self._dataloader = self.valid_dataloader if split == 'valid' else self.test_dataloader

        #if model is None:
        #	print("No pre-defined model!")
        #	self._build_model()

    def _build_dataloader(self, do_valid=False, do_test=False):

        if do_valid:
            self.valid_dataset = ResponseSelectionDataset(
                self.hparams,
                split="valid",
            )
            self.valid_dataloader = DataLoader(
                self.valid_dataset,
                batch_size=self.hparams.eval_batch_size,
                num_workers=self.hparams.cpu_workers,
                drop_last=False,
            )

        if do_test:
            self.test_dataset = ResponseSelectionDataset(
                self.hparams,
                split="test",
            )

            self.test_dataloader = DataLoader(
                self.test_dataset,
                batch_size=self.hparams.eval_batch_size,
                num_workers=self.hparams.cpu_workers,
                drop_last=False,
            )

    def _build_model(self):
        self.model = Model(self.hparams)
        self.model = self.model.to(self.device)
        # Use Multi-GPUs
        if -1 not in self.hparams.gpu_ids and len(self.hparams.gpu_ids) > 1:
            self.model = nn.DataParallel(self.model, self.hparams.gpu_ids)

    def run_evaluate(self, evaluation_path):
        self._logger.info("Evaluation")
        #model_state_dict, optimizer_state_dict = load_checkpoint(evaluation_path)

        # 		if isinstance(self.model, nn.DataParallel):
        # 			self.model.module.load_state_dict(model_state_dict)
        # 		else:
        # 			self.model.load_state_dict(model_state_dict)

        k_list = self.hparams.recall_k_list
        total_mrr = 0
        #total_R_10 =[0.0]*len(k_list)
        total_examples, total_correct = 0, 0
        #self.model.eval()
        with torch.no_grad():
            for batch_idx, batch in enumerate(tqdm(self._dataloader)):
                print(batch_idx)
                buffer_batch = batch.copy()
                for key in batch:
                    print(batch[key])
                    print(key)            


In [4]:

import os
import argparse
import collections
import logging
from datetime import datetime
arg_parser = argparse.ArgumentParser(description="Bert / Response Selection (PyTorch)")
arg_parser.add_argument("--model", dest="model", type=str,
                      default="bert_base",
                      help="Model Name")
arg_parser.add_argument("--root_dir", dest="root_dir", type=str,
                      default="./results_v1",
                      help="model train logs, checkpoints")
arg_parser.add_argument("--data_dir", dest="data_dir", type=str,
                      default="./data/ubuntu_corpus_v1/%s_%s.pkl",
                      help="ubuntu corpus v1 pkl path") # ubuntu_train.pkl, ubuntu_valid_pkl, ubuntu_test.pkl
arg_parser.add_argument("--bert_pretrained_dir", dest="bert_pretrained_dir", type=str,
                      default="./resources",
                      help="bert pretrained directory")
arg_parser.add_argument("--bert_pretrained", dest="bert_pretrained", type=str,
                      default="bert-post-uncased",
                      help="bert pretrained directory")  # bert-base-uncased, bert-post-uncased -> under bert_pretrained_dir
arg_parser.add_argument("--train_type", dest="train_type", type=str,
                      default="fine_tuning",
                      help="Train type") # fine_tuning, post_training
arg_parser.add_argument("--evaluate", dest="evaluate", type=str,
                      help="Evaluation Checkpoint", default="")

args = arg_parser.parse_known_args()[0]

In [12]:

from config.hparams import *
from data.data_utils import InputExamples
#from train import ResponseSelection
from post_train import BERTDomainPostTraining

PARAMS_MAP = {
# fine-tuning (ft)
"bert_base_ft" : BASE_PARAMS,
"bert_dpt_ft" : DPT_FINETUNING_PARAMS,

# post-training (pt)
"bert_ubuntu_pt" : POST_TRAINING_PARAMS,
}


hparams = PARAMS_MAP['bert_base_ft']
hparams["root_dir"] = args.root_dir
root_dir = os.path.join(hparams["root_dir"], args.model, args.train_type, "eval")


hparams["data_dir"] = args.data_dir
hparams["bert_pretrained_dir"] = args.bert_pretrained_dir
#hparams["bert_pretrained"] = args.bert_pretrained

hparams = collections.namedtuple("HParams", sorted(hparams.keys()))(**hparams)
print('22222222222222222222')
print(args.data_dir)
print(args.evaluate)

model = Evaluation(hparams)
model.run_evaluate(args.evaluate)

22222222222222222222
./data/ubuntu_corpus_v1/%s_%s.pkl

Evaluation Split : test
100000 examples has been loaded!
200000 examples has been loaded!
300000 examples has been loaded!
400000 examples has been loaded!
500000 examples has been loaded!
total test examples 500000
./resources/bert-base-uncased
./resources/bert-base-uncased/bert-base-uncased-vocab.txt


  0%|          | 9/5000 [00:02<2:03:31,  1.48s/it]

0
tensor([[ 101, 4658, 2036,  ...,    0,    0,    0],
        [ 101, 4658, 2036,  ...,    0,    0,    0],
        [ 101, 4658, 2036,  ...,    0,    0,    0],
        ...,
        [ 101, 2003, 2009,  ...,    0,    0,    0],
        [ 101, 2003, 2009,  ...,    0,    0,    0],
        [ 101, 2003, 2009,  ..., 2065, 2049,  102]])
anno_sent
tensor([[0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        ...,
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 1, 1, 1]])
segment_ids
tensor([[1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        ...,
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 1, 1, 1]])
attention_mask
tensor([1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 1., 0., 0., 0.,

  1%|          | 26/5000 [00:02<1:00:58,  1.36it/s]

16
tensor([[  101,  2053, 20385,  ...,     0,     0,     0],
        [  101,  2053, 20385,  ...,     0,     0,     0],
        [  101,  2053, 20385,  ...,     0,     0,     0],
        ...,
        [  101,  2417, 12707,  ...,     0,     0,     0],
        [  101,  2417, 12707,  ...,     0,     0,     0],
        [  101,  2417, 12707,  ...,     0,     0,     0]])
anno_sent
tensor([[0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        ...,
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0]])
segment_ids
tensor([[1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        ...,
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0]])
attention_mask
tensor([1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0.,
  

...

100%|█████████▉| 4981/5000 [01:12<00:00, 57.00it/s]

4972
tensor([[  101,  2074,  1037,  ...,     0,     0,     0],
        [  101,  2074,  1037,  ...,     0,     0,     0],
        [  101,  2074,  1037,  ...,     0,     0,     0],
        ...,
        [  101, 20648,  1037,  ...,     0,     0,     0],
        [  101, 20648,  1037,  ...,     0,     0,     0],
        [  101, 20648,  1037,  ...,     0,     0,     0]])
anno_sent
tensor([[0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        ...,
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0]])
segment_ids
tensor([[1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        ...,
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0]])
attention_mask
tensor([1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0.,


100%|█████████▉| 4996/5000 [01:13<00:00, 62.31it/s]

tensor([[0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        ...,
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0],
        [0, 0, 0,  ..., 0, 0, 0]])
segment_ids
tensor([[1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        ...,
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0],
        [1, 1, 1,  ..., 0, 0, 0]])
attention_mask
tensor([1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0.,
        0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0.,
        0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0.,
        0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        1., 0., 0., 0., 0., 0., 0., 0., 0., 0.])
label
4984
tensor([[ 101, 1045, 1049,  ...,    0,    0,    0],
        [ 101, 1045, 1049

100%|██████████| 5000/5000 [01:13<00:00, 67.93it/s]
